# Applied Data Science Capstone: Segmenting and Clustering neighborhoods in Toronto

## Web Scraping with Beautiful Soup

Importing needed libraries for web scraping with Beautiful Soup and creating data frame:

In [1]:
import pandas as pd
import numpy as np
import requests
from bs4 import BeautifulSoup

Information on Toronto postal codes, boroughs and neighborhoods from wikipedia. Definition of url and variable 'data':

In [2]:
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
data  = requests.get(url).text

Creating a soup object using variable 'data':

In [3]:
soup = BeautifulSoup(data,"html5lib") 

Web scraping and generating pandas data frame:

In [4]:
table_contents=[]
table=soup.find('table')
for row in table.findAll('td'):
    cell = {}
    if row.span.text=='Not assigned':
        pass
    else:
        cell['PostalCode'] = row.p.text[:3]
        cell['Borough'] = (row.span.text).split('(')[0]
        cell['Neighborhood'] = (((((row.span.text).split('(')[1]).strip(')')).replace(' /',',')).replace(')',' ')).strip(' ')
        table_contents.append(cell)

# print(table_contents)
df=pd.DataFrame(table_contents)
df['Borough']=df['Borough'].replace({'Downtown TorontoStn A PO Boxes25 The Esplanade':'Downtown Toronto Stn A',
                                             'East TorontoBusiness reply mail Processing Centre969 Eastern':'East Toronto Business',
                                             'EtobicokeNorthwest':'Etobicoke Northwest','East YorkEast Toronto':'East York/East Toronto',
                                             'MississaugaCanada Post Gateway Processing Centre':'Mississauga'})

In [5]:
df.head()

PostalCode           Borough                      Neighborhood
0        M3A        North York                         Parkwoods
1        M4A        North York                  Victoria Village
2        M5A  Downtown Toronto         Regent Park, Harbourfront
3        M6A        North York  Lawrence Manor, Lawrence Heights
4        M7A      Queen's Park     Ontario Provincial Government

In [6]:
df.shape

(103, 3)

## Get coordinates of neighborhoods

Download csv file with coordinates as dataframe 'coords':

In [7]:
coords = pd.read_csv('https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs_v1/Geospatial_Coordinates.csv')
coords.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [8]:
coords.shape

(103, 3)

Rename Postal Code column in coords to match with df:

In [9]:
coords.rename(columns={"Postal Code": "PostalCode"}, inplace=True)
coords.head()

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

Merge the dataframes with PostalCode as key:

In [10]:
df=pd.merge(df, coords, left_on = 'PostalCode', right_on = 'PostalCode', how = 'left')

In [11]:
df.shape

(103, 5)

In [12]:
df.head()

PostalCode           Borough                      Neighborhood   Latitude  \
0        M3A        North York                         Parkwoods  43.753259   
1        M4A        North York                  Victoria Village  43.725882   
2        M5A  Downtown Toronto         Regent Park, Harbourfront  43.654260   
3        M6A        North York  Lawrence Manor, Lawrence Heights  43.718518   
4        M7A      Queen's Park     Ontario Provincial Government  43.662301   

   Longitude  
0 -79.329656  
1 -79.315572  
2 -79.360636  
3 -79.464763  
4 -79.389494

## Explore and Cluster neighborhoods

Import libraries:

In [13]:
import folium
from geopy.geocoders import Nominatim
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans

Turn on option for displaying all columns and rows of dataframes:

In [14]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

Get latitude and longitude for Toronto:

In [15]:
address = 'Toronto'

geolocator = Nominatim(user_agent="toronto")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


Map all neighborhoods:

In [16]:
# create map of Toronnto using latitude and longitude values from cell above
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add neighborhood markers to map
for lat, lng, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood']):
    label = '{}, {}'.format(df, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

The following clustering and analysis of Toronto neighborhoods will contain all neighborhoods displayed in above map.

Define Foursquare API

In [38]:
CLIENT_ID = '' # my Foursquare ID
CLIENT_SECRET = '' # my Foursquare Secret
ACCESS_TOKEN = '' #my access token
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value
radius = 500

print('Credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)
print('ACCESS_TOKEN:' + ACCESS_TOKEN)

Credentials:
CLIENT_ID: 
CLIENT_SECRET:
ACCESS_TOKEN:


Get information on nearby venues for all neighborhoods from Foursquare

In [18]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [19]:
toronto_venues = getNearbyVenues(names=df['Neighborhood'], latitudes=df['Latitude'], longitudes=df['Longitude'], radius=500)


Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Ontario Provincial Government
Islington Avenue
Malvern, Rouge
Don Mills North
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
The Danforth  East
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmount Park
Bayview Village
Downsview East
The Danforth

Analyze resulting dataframe:

In [20]:
#Number of venues and first 5 rows of the dataframe:
print(toronto_venues.shape)
toronto_venues.head()

(2114, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3               Portugril       43.725819       -79.312785   
4             Tim Hortons       43.725517       -79.313103   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3  Portuguese Restaurant  
4            Coffee Shop

Analyze number of venues per neighborhood:

In [21]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               4   
Alderwood, Long Branch                                                  7   
Bathurst Manor, Wilson Heights, Downsview North                        21   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      25   
Berczy Park                                                            59   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           25   
CN Tower, King and Spadina, Railway Lands, Harb...                     16   
Caledonia-Fairbanks                                                     4   
Cedarbrae                                                               8   
Central Bay Street                                                     66   
Christie                                                               16   
Church and Wellesley                                                   73   
Clairville, Humberwood, Woodbine Downs, West Hu...                      5   
Clarks Corners, Tam O'Shanter, Sullivan                                12   
Cliffside, Cliffcrest, Scarborough Village West                         3   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             34   
Davisville North                                                        8   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        4   
Don Mills North                                                         5   
Don Mills South                                                        19   
Dorset Park, Wexford Heights, Scarborough Town ...                      5   
Downsview Central                                                       3   
Downsview East                                                          2   
Downsview Northwest                                                     4   
Downsview West                                                          5   
Dufferin, Dovercourt Village                                           14   
Enclave of L4W                                                         14   
Enclave of M4L                                                         18   
Enclave of M5E                                                         97   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      9   
Fairview, Henry Farm, Oriole                                           68   
First Canadian Place, Underground city                                100   
Forest Hill North & West                                                4   
Garden District, Ryerson                                              100   
Glencairn                                                               5   
Golden Mile, Clairlea, Oakridge                                         8   
Guildwood, Morningside, West Hill                                       9   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          24   
Hillcrest Village                                                       5   
Humber Summit                                                           4   
Humberlea, Emery                                                        1   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         21   
Kennedy Park, Ionview, East Birchmount Park                             5   
Kensington Market, Chinatown, Grange Park                              65   
Kingsview Village, St. Phillips, Martin Grove G...                      4   
Lawrence Manor, Lawrence Heights                

Count number of unique venue categories

In [22]:
print('{} unique categories.'.format(len(toronto_venues['Venue Category'].unique())))

262 unique categories.


Create dataframe of venue categories and occurences per neighborhood:

In [41]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

print(toronto_onehot.shape)
toronto_onehot.head()

(2114, 262)


Yoga Studio  Accessories Store  Airport  Airport Food Court  Airport Gate  \
0            0                  0        0                   0             0   
1            0                  0        0                   0             0   
2            0                  0        0                   0             0   
3            0                  0        0                   0             0   
4            0                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Garage  Auto Workshop  \
0                 0                   0            0              0   
1                 0                   0            0              0   
2                 0                   0            0              0   
3                 0                   0            0              0   
4                 0                   0            0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0                 0                   0      0                0         0   
1                 0                   0      0                0         0   
2                 0                   0      0                0         0   
3                 0                   0      0                0         0   
4                 0                   0      0                0         0   

   Beer Store  Belgian Restaurant  Bike Shop  Bistro  Boat or Ferry  \
0           0                   0          0       0              0   
1           0                   0          0       0              0   
2           0                   0          0       0              0   
3           0                   0          0       0              0   
4           0                   0          0       0              0   

   Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  \
0          0         0                     0               0        0   
1          0         0                     0               0        0   
2          0         0                     0               0        0   
3          0         0                     0               0        0   
4          0         0                     0               0        0   

   Bridal Shop  Bubble Tea Shop  Building  Burger Joint  Burrito Place  \
0            0                0         0             0              0   
1            0                0         0             0              0   
2            0                0         0             0              0   
3            0                0         0             0              0   
4            0                0

Group by neighborhoods:

In [24]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                           Agincourt     0.000000   
1                              Alderwood, Long Branch     0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North     0.000000   
3                                     Bayview Village     0.000000   
4                   Bedford Park, Lawrence Manor East     0.000000   
5                                         Berczy Park     0.000000   
6                         Birch Cliff, Cliffside West     0.000000   
7        Brockton, Parkdale Village, Exhibition Place     0.040000   
8   CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
9                                 Caledonia-Fairbanks     0.000000   
10                                          Cedarbrae     0.000000   
11                                 Central Bay Street     0.015152   
12                                           Christie     0.000000   
13                               Church and Wellesley     0.027397   
14  Clairville, Humberwood, Woodbine Downs, West H...     0.000000   
15            Clarks Corners, Tam O'Shanter, Sullivan     0.000000   
16    Cliffside, Cliffcrest, Scarborough Village West     0.000000   
17                     Commerce Court, Victoria Hotel     0.000000   
18                                         Davisville     0.000000   
19                                   Davisville North     0.000000   
20   Del Ray, Mount Dennis, Keelsdale and Silverthorn     0.000000   
21                                    Don Mills North     0.000000   
22                                    Don Mills South     0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...     0.000000   
24                                  Downsview Central     0.000000   
25                                     Downsview East     0.000000   
26                                Downsview Northwest     0.000000   
27                                     Downsview West     0.000000   
28                       Dufferin, Dovercourt Village     0.000000   
29                                     Enclave of L4W     0.000000   
30                                     Enclave of M4L     0.055556   
31                                     Enclave of M5E     0.010309   
32  Eringate, Bloordale Gardens, Old Burnhamthorpe...     0.000000   
33                       Fairview, Henry Farm, Oriole     0.000000   
34             First Canadian Place, Underground city     0.000000   
35                           Forest Hill North & West     0.000000   
36                           Garden District, Ryerson     0.000000   
37                                          Glencairn     0.000000   
38                    Golden Mile, Clairlea, Oakridge     0.000000   
39                  Guildwood, Morningside, West Hill     0.000000   
40  Harbourfront East, Union Station, Toronto Islands     0.000000   
41                      High Park, The Junction South     0.000000   
42                                  Hillcrest Village     0.000000   
43                                      Humber Summit     0.000000   
44                                   Humberlea, Emery     0.000000   
45                                 Humewood-Cedarvale     0.000000   
46                     India Bazaar, The Beaches West     0.000000   
47        Kennedy Park, Ionview, East Birchmount Park     0.000000   
48          Kensington Market, Chinatown, Grange Park     0.000000   
49  Kingsview Village, St. Phillips, Martin Grove ...     0.000000   
50                   Lawrence Manor, Lawrence Heights     0.000000   
51                                      Lawrence Park     0.000000   
52                                            Leaside     0.000000   
53                           Little Portugal, Trinity     0.022727   
54                                     Malvern, Rouge     0.000000   
55  Milliken, Agincourt North, Steeles East, L'Amo...     0.000000   
56  Mimico NW, The Queensway West, South of Bloor,.

Create dataframe with top 10 venues per neighborhood

In [25]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

print(neighborhoods_venues_sorted.shape)
neighborhoods_venues_sorted.head()

(99, 11)


Neighborhood 1st Most Common Venue  \
0                                        Agincourt                Lounge   
1                           Alderwood, Long Branch           Pizza Place   
2  Bathurst Manor, Wilson Heights, Downsview North                  Bank   
3                                  Bayview Village    Chinese Restaurant   
4                Bedford Park, Lawrence Manor East    Italian Restaurant   

  2nd Most Common Venue 3rd Most Common Venue      4th Most Common Venue  \
0        Breakfast Spot        Clothing Store  Latin American Restaurant   
1                   Gym           Coffee Shop                 Playground   
2           Coffee Shop              Pharmacy                Pizza Place   
3                  Bank   Japanese Restaurant                       Café   
4           Coffee Shop        Sandwich Place           Sushi Restaurant   

       5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0       Ethiopian Restaurant           Escape Room     Electronics Store   
1                        Pub        Sandwich Place         Women's Store   
2  Middle Eastern Restaurant            Restaurant                 Diner   
3              Women's Store      Doner Restaurant        Discount Store   
4            Thai Restaurant                   Pub                  Café   

         8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0  Eastern European Restaurant    Dim Sum Restaurant    Dumpling Restaurant  
1          Distribution Center          Dessert Shop     Dim Sum Restaurant  
2          Fried Chicken Joint    Frozen Yogurt Shop          Deli / Bodega  
3          Distribution Center               Dog Run             Donut Shop  
4            Indian Restaurant                   Spa   Fast Food Restaurant

Clustering: Create 5 clusters

In [26]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 3])

In [27]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df

# merge toronto_grouped with df to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head()

PostalCode           Borough                      Neighborhood   Latitude  \
0        M3A        North York                         Parkwoods  43.753259   
1        M4A        North York                  Victoria Village  43.725882   
2        M5A  Downtown Toronto         Regent Park, Harbourfront  43.654260   
3        M6A        North York  Lawrence Manor, Lawrence Heights  43.718518   
4        M7A      Queen's Park     Ontario Provincial Government  43.662301   

   Longitude  Cluster Labels   1st Most Common Venue 2nd Most Common Venue  \
0 -79.329656             3.0                    Park     Food & Drink Shop   
1 -79.315572             0.0   Portuguese Restaurant          Hockey Arena   
2 -79.360636             0.0             Coffee Shop                   Pub   
3 -79.464763             0.0  Furniture / Home Store        Clothing Store   
4 -79.389494             0.0             Coffee Shop      Sushi Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0         Women's Store            Donut Shop                 Diner   
1          Intersection           Pizza Place           Coffee Shop   
2                Bakery                  Park                  Café   
3           Coffee Shop              Boutique    Miscellaneous Shop   
4                  Bank                   Bar              Beer Bar   

  6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0        Discount Store   Distribution Center                Dog Run   
1    Dim Sum Restaurant                 Diner         Discount Store   
2        Breakfast Spot               Theater   Gym / Fitness Center   
3         Women's Store     Accessories Store  Vietnamese Restaurant   
4         Smoothie Shop        Sandwich Place           Burger Joint   

        9th Most Common Venue 10th Most Common Venue  
0            Doner Restaurant              Drugstore  
1         Distribution Center                Dog Run  
2           Electronics Store             Restaurant  
3  Construction & Landscaping     Dim Sum Restaurant  
4               Burrito Place                   Café

In [28]:
toronto_merged.shape

(103, 16)

Remove N/As:

In [29]:
toronto_merged.dropna(inplace=True)
toronto_merged.shape

(99, 16)

Create map of clusters:

In [30]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Clustering results in 5 clusters (0 - 4), whereby cluster 0 contains many neighborhoods and cluster 3 several. The other clusters contain only 1 neighborhood.

Examine Cluster 0

In [33]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels  \
1                                     Victoria Village             0.0   
2                            Regent Park, Harbourfront             0.0   
3                     Lawrence Manor, Lawrence Heights             0.0   
4                        Ontario Provincial Government             0.0   
6                                       Malvern, Rouge             0.0   
7                                      Don Mills North             0.0   
8                      Parkview Hill, Woodbine Gardens             0.0   
9                             Garden District, Ryerson             0.0   
10                                           Glencairn             0.0   
13                                     Don Mills South             0.0   
14                                    Woodbine Heights             0.0   
15                                      St. James Town             0.0   
16                                  Humewood-Cedarvale             0.0   
17   Eringate, Bloordale Gardens, Old Burnhamthorpe...             0.0   
18                   Guildwood, Morningside, West Hill             0.0   
19                                         The Beaches             0.0   
20                                         Berczy Park             0.0   
22                                              Woburn             0.0   
23                                             Leaside             0.0   
24                                  Central Bay Street             0.0   
25                                            Christie             0.0   
26                                           Cedarbrae             0.0   
27                                   Hillcrest Village             0.0   
28     Bathurst Manor, Wilson Heights, Downsview North             0.0   
29                                    Thorncliffe Park             0.0   
30                            Richmond, Adelaide, King             0.0   
31                        Dufferin, Dovercourt Village             0.0   
32                                 Scarborough Village             0.0   
33                        Fairview, Henry Farm, Oriole             0.0   
34                     Northwood Park, York University             0.0   
36   Harbourfront East, Union Station, Toronto Islands             0.0   
37                            Little Portugal, Trinity             0.0   
38         Kennedy Park, Ionview, East Birchmount Park             0.0   
39                                     Bayview Village             0.0   
41                        The Danforth West, Riverdale             0.0   
42            Toronto Dominion Centre, Design Exchange             0.0   
43        Brockton, Parkdale Village, Exhibition Place             0.0   
44                     Golden Mile, Clairlea, Oakridge             0.0   
46                                      Downsview West             0.0   
47                      India Bazaar, The Beaches West             0.0   
48                      Commerce Court, Victoria Hotel             0.0   
49            North Park, Maple Leaf Park, Upwood Park             0.0   
50                                       Humber Summit             0.0   
51     Cliffside, Cliffcrest, Scarborough Village West             0.0   
53                                   Downsview Central             0.0   
54                                     Studio District             0.0   
55                   Bedford Park, Lawrence Manor East             0.0   
56    Del Ray, Mount Dennis, Keelsdale and Silverthorn             0.0   
58                         Birch Cliff, Cliffside West             0.0   
59                                    Willowdale South             0.0   
60                                 Downsview Northwest             0.0   
61                                       Lawrence Park             0.0   
62                                            Roselawn             0.0   
63                       Runnymede, The Juncti

Common to cluster 0 is the presence of restaurants, bars and coffee shops.

Examine Cluster 3

In [37]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels  \
0                                           Parkwoods             3.0   
21                                Caledonia-Fairbanks             3.0   
35                                 The Danforth  East             3.0   
40                                     Downsview East             3.0   
64                                             Weston             3.0   
66                                    York Mills West             3.0   
85  Milliken, Agincourt North, Steeles East, L'Amo...             3.0   
91                                           Rosedale             3.0   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                   Park     Food & Drink Shop         Women's Store   
21                  Park         Women's Store                  Pool   
35                  Park     Convenience Store         Women's Store   
40                  Park               Airport         Women's Store   
64                  Park         Jewelry Store     Convenience Store   
66                  Park     Convenience Store         Women's Store   
85                  Park            Playground          Intersection   
91                  Park            Playground                 Trail   

   4th Most Common Venue        5th Most Common Venue 6th Most Common Venue  \
0             Donut Shop                        Diner        Discount Store   
21      Doner Restaurant           Dim Sum Restaurant                 Diner   
35            Donut Shop                        Diner        Discount Store   
40            Donut Shop                        Diner        Discount Store   
64         Women's Store               Discount Store   Distribution Center   
66            Donut Shop                        Diner        Discount Store   
85      Doner Restaurant           Dim Sum Restaurant                 Diner   
91     Electronics Store  Eastern European Restaurant           Escape Room   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0    Distribution Center               Dog Run      Doner Restaurant   
21        Discount Store   Distribution Center               Dog Run   
35   Distribution Center               Dog Run      Doner Restaurant   
40   Distribution Center               Dog Run      Doner Restaurant   
64               Dog Run      Doner Restaurant            Donut Shop   
66   Distribution Center               Dog Run      Doner Restaurant   
85        Discount Store   Distribution Center               Dog Run   
91   Dumpling Restaurant             Drugstore            Donut Shop   

   10th Most Common Venue  
0               Drugstore  
21              Drugstore  
35    Dumpling Restaurant  
40    Dumpling Restaurant  
64    Dumpling Restaurant  
66    Dumpling Restaurant  
85             Donut Shop  
91          Deli / Bodega

Common to cluster 3 is the presence of parks and stores.

The clusters containing only 1 neighborhood are not further analyzed.